# Statistics for Nanna's email of 2019-02-13

Hi Herbert,

you would be a lifesaver if you could give me some updated information about the following (regarding the Stimmen database):

- what's the latest breakdown of age, gender, most active language distribution in all the data, for the prediction data, and for the recording data?
- How many individual users are there in the corpus of picture task recordings?
- How many users have made recordings in more than one language? (and if possible a list with the device ids)
- it would be great to have the breakdown of amounts of quiz taking over the months - so how many in september 2017, october 2017, and so on up until september 2018

Any luck with any of these would be a massive help. I only need the data from 19 September 2017 onwards,

Nanna

In [1]:
# Enable portforwording from 3307 locally to 3306 on the stimmen database machine
# ssh -L 3307:127.0.0.1:3306 stimmen.housing.rug.nl

import pandas
import MySQLdb
from collections import defaultdict, Counter
from ipy_table import make_table, set_row_style
from IPython.display import display

from getpass import getpass

if 'mysql_password' not in globals():
    mysql_password = getpass()

db = MySQLdb.connect(host='127.0.0.1', port=3307, user='stimmen', passwd=mysql_password, db='stimmen', charset='utf8')

········


In [2]:
# Kind reminded of the table names
print('\n'.join(
    table
    for table in pandas.read_sql('''show tables;''', db)['Tables_in_stimmen']
    if table.startswith('core_')
))

core_freespeechresult
core_freespeechtheme
core_language
core_picturegameitem
core_picturegameresult
core_predictionquizresult
core_predictionquizresultquestionanswer
core_surveyanswer
core_surveyquestion
core_surveyquestioncategory
core_surveyresult
core_surveyresultquestionanswer


### What's the latest breakdown of age, gender, most active language distribution in all the data, for the prediction data, and for the recording data?

In [3]:
def remove_repeating(rows, columns=[0]):
    """Empty cells which are the same as the cell above
    (in the previous row) for the specified columns, to create
    a less redunant and more readable table"""
    return [
        [
            '' if column == column_ and i in columns else column
            for i, (column, column_) in enumerate(zip(row, row_))
        ]
        for row, row_ in zip(rows, [[None] * len(rows[0])] + rows)
    ]

In [4]:
for gametype in ['prediction quiz', 'picture game', 'free speech']:
    demographics = pandas.read_sql('''
        SELECT 
            answer.question_text AS question,
            answer.answer_text AS answer,
            game.id AS game_id,
            game.survey_result_id AS survey_id
        FROM core_{gametype}result AS game
        LEFT JOIN core_surveyresultquestionanswer AS answer
            ON answer.survey_result_id = game.survey_result_id
        WHERE submitted_at > '2017-09-19'
    '''.format(
        gametype=gametype.replace(' ', '')
    ), db)
    
    table = [
        [
            question_text,
            question_answer,
            len(records)
        ]
        for question_text, answers in demographics.groupby('question')
        for question_answer, records in answers.groupby('answer')
    ]

    n_participants = len(demographics['game_id'].unique())
    n_no_survey = len(demographics[demographics['question'].isna()]['game_id'].unique())
    n_with_survey = len(demographics[~demographics['question'].isna()]['game_id'].unique())

    make_table(
        [
            [gametype, '', ''],
            ['question', 'answer', 'count'],
            ['Total participants', '', n_participants],
            ['No survey', '', n_no_survey],
            ['With survey', '', n_with_survey],
            ['', '', '']
        ] + [
            [question, 'total answers', len(answers_)]
            for question, answers_ in demographics.groupby('question')
        ] + [['', '', '']] +
        remove_repeating(sorted(table, key=lambda x: (x[0], -x[2])))
    )
    set_row_style(1, bold=True)
    display(set_row_style(0, bold=True))

### How many individual users are there in the corpus of picture task recordings?

The `core_picturegameresult` table has a `survey_result_id` and a `session_id` to distinguish users. Some sessions have multiple surveys and vice versa. So I figured the survey is the fairest way to distinguish them.

In [5]:
pandas.read_sql('''
    SELECT COUNT(DISTINCT survey_result_id), COUNT(DISTINCT session_id), COUNT(*)
    FROM core_picturegameresult
    WHERE submitted_at > "2017-09-19"
''', db)

COUNT(DISTINCT survey_result_id)  COUNT(DISTINCT session_id)  COUNT(*)
0                              1930                       24695     41655

### How many users have made recordings in more than one language?

* and if possible a list with the device ids
* it would be great to have the breakdown of amounts of quiz taking over the months: sep-17, oct-17, ..., sep-18

There are not so many, these are the ones:

In [6]:
pandas.read_sql('''
    SELECT
        CONCAT(YEAR(result.submitted_at), '-', MONTH(result.submitted_at)) AS 'year-month',
        COUNT(*) AS '# games',
        COUNT(DISTINCT result.survey_result_id) AS '# surveys',
        GROUP_CONCAT(DISTINCT lang.name SEPARATOR ',') AS 'languages'
    FROM core_freespeechresult AS result
    LEFT JOIN core_language as lang
      ON lang.id = result.language_id
    WHERE submitted_at > "2017-09-19"
    AND result.survey_result_id IN (
        SELECT result.survey_result_id
        FROM core_freespeechresult AS result
        WHERE submitted_at > "2017-09-19"
        GROUP BY result.survey_result_id
        HAVING COUNT(DISTINCT result.language_id) > 1
    )
    GROUP BY YEAR(result.submitted_at), MONTH(result.submitted_at)
''', db)

year-month  # games  # surveys                           languages
0     2017-9        7          2  English,Nederlands,Frysk,Stadsfrys
1    2017-10        7          2           Frysk,Hielpers,Nederlands
2    2017-11       10          4    Nederlands,Frysk,Français,Sranan
3    2017-12        2          1                    Frysk,Nederlands
4     2018-4        2          1                Stadsfrys,Nederlands
5    2018-11        2          1                 Gronings,Nederlands

The device ids:

In [7]:
pandas.read_sql('''
    SELECT
        DISTINCT survey.device_id
    FROM core_freespeechresult AS result
    LEFT JOIN core_language as lang
      ON lang.id = result.language_id
    LEFT JOIN core_surveyresult as survey
      ON survey.id = result.survey_result_id
    WHERE result.submitted_at > "2017-09-19"
    AND result.survey_result_id IN (
        SELECT result.survey_result_id
        FROM core_freespeechresult AS result
        WHERE result.submitted_at > "2017-09-19"
        GROUP BY result.survey_result_id
        HAVING COUNT(DISTINCT result.language_id) > 1
    )
''', db)

device_id
0   738191E5-80E4-4D07-A15E-6B7DE881906A
1                       fb28928ef1703592
2   820E203F-1B70-40A8-BD47-04681D07BC9C
3                       1aa95d23fddf3827
4   F95F07AE-B524-4256-9171-F7FFA9E49156
5   C8F56303-E912-4BC3-AD51-E1CA8B425AE9
6   B653C16D-BDA8-4A47-BC6A-C3171D89AF71
7                       b40fb5e73d431e6b
8   C9FD6142-A64A-4AD8-B317-3BB833A11667
9   A258D9E9-FD32-4A97-A5A1-A4B72ADFC71D
10                      8190723c74b4b0bf

The results:

In [8]:
pandas.read_sql('''
    SELECT
        survey.device_id,
        lang.name as language,
        result.*
    FROM core_freespeechresult AS result
    LEFT JOIN core_language as lang
      ON lang.id = result.language_id
    LEFT JOIN core_surveyresult as survey
      ON survey.id = result.survey_result_id
    WHERE result.submitted_at > "2017-09-19"
    AND result.survey_result_id IN (
        SELECT result.survey_result_id
        FROM core_freespeechresult AS result
        WHERE submitted_at > "2017-09-19"
        GROUP BY result.survey_result_id
        HAVING COUNT(DISTINCT result.language_id) > 1
    )
''', db)

device_id    language   id  \
0   738191E5-80E4-4D07-A15E-6B7DE881906A   Stadsfrys  159   
1   738191E5-80E4-4D07-A15E-6B7DE881906A   Stadsfrys  160   
2   738191E5-80E4-4D07-A15E-6B7DE881906A       Frysk  161   
3                       fb28928ef1703592       Frysk  221   
4                       fb28928ef1703592       Frysk  222   
5                       fb28928ef1703592  Nederlands  223   
6                       fb28928ef1703592     English  224   
7   820E203F-1B70-40A8-BD47-04681D07BC9C  Nederlands  333   
8   820E203F-1B70-40A8-BD47-04681D07BC9C  Nederlands  334   
9   820E203F-1B70-40A8-BD47-04681D07BC9C       Frysk  335   
10                      1aa95d23fddf3827       Frysk  373   
11                      1aa95d23fddf3827       Frysk  374   
12                      1aa95d23fddf3827    Hielpers  375   
13                      1aa95d23fddf3827       Frysk  376   
14  F95F07AE-B524-4256-9171-F7FFA9E49156       Frysk  388   
15  F95F07AE-B524-4256-9171-F7FFA9E49156       Frysk  389   
16  F95F07AE-B524-4256-9171-F7FFA9E49156       Frysk  390   
17  F95F07AE-B524-4256-9171-F7FFA9E49156      Sranan  391   
18  C8F56303-E912-4BC3-AD51-E1CA8B425AE9       Frysk  410   
19  B653C16D-BDA8-4A47-BC6A-C3171D89AF71       Frysk  411   
20  B653C16D-BDA8-4A47-BC6A-C3171D89AF71  Nederlands  412   
21  C8F56303-E912-4BC3-AD51-E1CA8B425AE9  Nederlands  414   
22                      b40fb5e73d431e6b       Frysk  426   
23                      b40fb5e73d431e6b    Français  428   
24  C9FD6142-A64A-4AD8-B317-3BB833A11667  Nederlands  452   
25  C9FD6142-A64A-4AD8-B317-3BB833A11667       Frysk  453   
26  A258D9E9-FD32-4A97-A5A1-A4B72ADFC71D  Nederlands  476   
27  A258D9E9-FD32-4A97-A5A1-A4B72ADFC71D   Stadsfrys  477   
28                      8190723c74b4b0bf  Nederlands  500   
29                      8190723c74b4b0bf    Gronings  501   

                                         session_id app_locale  \
0              6349CCA2-358F-4AE5-821F-543AD0B9C97A         fy   
1              ACEF45B4-3162-4A5F-B83A-3E39BE140117         fy   
2              ACEF45B4-3162-4A5F-B83A-3E39BE140117         fy   
3    androidSessionIdfb28928ef170359258404890608067         nl   
4    androidSessionIdfb28928ef170359258618421150746         nl   
5    androidSessionIdfb28928ef170359258714896361595         nl   
6    androidSessionIdfb28928ef170359259137367204559         nl   
7              28F45D4F-71F4-45A3-A9A2-B9813A16EC13         nl   
8              28F45D4F-71F4-45A3-A9A2-B9813A16EC13         nl   
9              28F45D4F-71F4-45A3-A9A2-B9813A16EC13         nl   
10  androidSessionId1aa95d23fddf3827591709392581151         fy   
11  androidSessionId1aa95d23fddf3827591856351721095         fy   
12  androidSessionId1aa95d23fddf3827592248608182404         fy   
13  androidSessionId1aa95d23fddf3827592854579719673         fy   
14             70BBF265-BB3B-4B53-8C1E-9B6CA179906C         fy   
15             70BBF265-BB3B-4B53-8C1E-9B6CA179906C         fy   
16             70BBF265-BB3B-4B53-8C1E-9B6CA179906C         fy   
17             70BBF265-BB3B-4B53-8C1E-9B6CA179906C         fy   
18             0D2F2AD3-177A-4991-AD5F-55CAF1BFDE35         nl   
19             07E90580-694C-4F9C-A82B-D431D88F6508         nl   
20             4CB961F7-432A-43EE-B748-41CB18DA6ACC         nl   
21             0D2F2AD3-177A-4991-AD5F-55CAF1BFDE35         nl   
22  androidSessionIdb40fb5e73d431e6b136597419729297         nl   
23  androidSessionIdb40fb5e73d431e6b136976454194882         nl   
24             9A976F40-ADF7-4F72-9C2F-9BD4F1AF4DF5         nl   
25             372127E4-AFFE-4BF5-BE7A-FF9D981F4D2E         nl   
26             63B8E61A-433A-433A-924F-0B2D9D6F0353         fy   
27             63B8E61A-433A-433A-924F-0B2D9D6F0353         fy   
28   androidSessionId8190723c74b4b0bf57887798554061         nl   
29   androidSessionId8190723c74b4b0bf58065148631545         nl   

          submitted_at                         theme_short_text  \
0  2017-09-20 21:05:47   

In [9]:
allcounts = dict()
tables = ['core_freespeechresult', 'core_picturegameresult', 'core_predictionquizresult', 'core_surveyresult']
for table in tables:
    counts = pandas.read_sql('''
        SELECT
            CONCAT(YEAR(result.submitted_at), '-', MONTH(result.submitted_at)) AS 'year-month',
            COUNT(*) AS '# games'
        FROM {table} AS result
        WHERE submitted_at > "2017-09-19"
        GROUP BY YEAR(result.submitted_at), MONTH(result.submitted_at)
    '''.format(table=table), db)
    allcounts[table] = dict(zip(
        ['-'.join('{:02d}'.format(int(d)) for d in date.split('-')) for date in counts['year-month']],
        counts['# games']
    ))
    
dates = sorted({
     date for dates in allcounts.values() for date in dates
})
make_table([[''] + tables] + [
    [date] + [allcounts[table].get(date, 0) for table in tables]
    for date in dates
])

In [10]:
make_table([
    [
        table,
        pandas.read_sql('''
            SELECT MAX(submitted_at) FROM {table}
        '''.format(table=table), db).values[0, 0],
        pandas.read_sql('''
            SELECT COUNT(*) FROM {table}
        '''.format(table=table), db).values[0, 0]
    ]
    for table in pandas.read_sql('''
        SHOW TABLES
    ''', db).values[:, 0]
    if 'submitted_at' in set(pandas.read_sql('''
            DESCRIBE {table}
        '''.format(table=table), db)['Field'])
])